In [1]:
import tensorflow as tf
import pandas as pd
import numpy as np

In [2]:
data=pd.read_csv('Iris.csv')
data.head()

Id  SepalLengthCm  SepalWidthCm  PetalLengthCm  PetalWidthCm      Species
0   1            5.1           3.5            1.4           0.2  Iris-setosa
1   2            4.9           3.0            1.4           0.2  Iris-setosa
2   3            4.7           3.2            1.3           0.2  Iris-setosa
3   4            4.6           3.1            1.5           0.2  Iris-setosa
4   5            5.0           3.6            1.4           0.2  Iris-setosa

In [3]:
data['y1']=0
data['y2']=0
data['y3']=0
for i in range(0,len(data['Species'])):
    if(data['Species'][i]=='Iris-versicolor'):
        data['y1'][i]=1
        data['y2'][i]=0
        data['y3'][i]=0
    elif(data['Species'][i]=='Iris-virginica'):
        data['y1'][i]=0
        data['y2'][i]=1
        data['y3'][i]=0
    else:
        data['y1'][i]=0
        data['y2'][i]=0
        data['y3'][i]=1
        

/home/cocoslabs/anaconda3/lib/python2.7/site-packages/ipykernel_launcher.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  
/home/cocoslabs/anaconda3/lib/python2.7/site-packages/ipykernel_launcher.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  from ipykernel import kernelapp as app
/home/cocoslabs/anaconda3/lib/python2.7/site-packages/ipykernel_launcher.py:16: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  app.launch_new_instance()
/home/cocoslabs/anaconda3/lib/python2.7/site-p

In [4]:
data.drop(['Id','Species'],inplace=True,axis=1)
data=data.sample(frac=1)
data.head()

SepalLengthCm  SepalWidthCm  PetalLengthCm  PetalWidthCm  y1  y2  y3
57             4.9           2.4            3.3           1.0   1   0   0
79             5.7           2.6            3.5           1.0   1   0   0
4              5.0           3.6            1.4           0.2   0   0   1
137            6.4           3.1            5.5           1.8   0   1   0
99             5.7           2.8            4.1           1.3   1   0   0

In [5]:
x=data.iloc[:,0:4].values
y=data.iloc[:,4:].values

In [6]:
X=tf.placeholder("float",[None,4])
Y=tf.placeholder("float",[None,3])

In [7]:
weights={
    'h1':tf.Variable(tf.random_normal([4,10])),
    'h2':tf.Variable(tf.random_normal([10,10])),
    'out':tf.Variable(tf.random_normal([10,3]))    
}
bias={
    'b1':tf.Variable(tf.random_normal([10])),
    'b2':tf.Variable(tf.random_normal([10])),
    'out':tf.Variable(tf.random_normal([3]))   
}

Instructions for updating:
Colocations handled automatically by placer.


### create model

In [8]:
layer1=tf.add(tf.matmul(X,weights['h1']),bias['b1'])
layer2=tf.add(tf.matmul(layer1,weights['h2']),bias['b2'])
model=tf.add(tf.matmul(layer2,weights['out']),bias['out'])

In [9]:
cross=tf.nn.softmax_cross_entropy_with_logits(logits=model,labels=Y)
loss=tf.reduce_mean(cross)

Instructions for updating:

Future major versions of TensorFlow will allow gradients to flow
into the labels input on backprop by default.

See `tf.nn.softmax_cross_entropy_with_logits_v2`.



In [10]:
optimizer = tf.train.AdamOptimizer(learning_rate=0.01)
train=optimizer.minimize(loss)

In [11]:
pred=tf.equal(tf.argmax(model,1),tf.argmax(Y,1))
acc=tf.reduce_mean(tf.cast(pred,tf.float32))

In [12]:
epoch=10000
init=tf.global_variables_initializer()
with tf.Session() as sess:
    sess.run(init)
    for i in range(epoch):
        print(sess.run(weights['h1']))
        sess.run(train,feed_dict={X:x,Y:y})
        losses=sess.run(loss,feed_dict={X:x,Y:y})
        accuracy=sess.run(acc,feed_dict={X:x,Y:y})    
        print('Epoch:{}/{} Loss:{:.3f} Accuracy:{:.3f}'.format(i+1,epoch,losses,accuracy))


[[-0.43755555  1.3031033   0.6748547  -0.71691835 -0.14097334 -0.9432672
  -0.94257015  2.132684   -2.3997312  -1.7006923 ]
 [-0.32290566 -1.0162941  -1.2342964   0.08061915 -2.4983404   0.37209743
   2.2587054  -1.7816005   1.2240365  -0.5465901 ]
 [ 0.57344264 -0.03531345 -0.23247117  0.52097195 -1.004098    0.96916795
  -0.2862747   0.10299512 -0.61811817 -1.9967811 ]
 [ 0.84128284  0.6127089  -0.79351676 -1.2811431   0.38950133 -0.6811394
   2.0528853   0.12926294 -0.48756447 -0.16000265]]
Epoch:1/10000 Loss:55.427 Accuracy:0.593
[[-0.42755556  1.3131033   0.6648547  -0.70691836 -0.13097334 -0.93326724
  -0.95257014  2.122684   -2.3897312  -1.6906923 ]
 [-0.31290567 -1.0062941  -1.2442964   0.09061915 -2.4883404   0.38209742
   2.2487054  -1.7916005   1.2340364  -0.5365901 ]
 [ 0.5834426  -0.02531345 -0.24247117  0.53097194 -0.99409807  0.97916794
  -0.2962747   0.09299512 -0.6081182  -1.9867811 ]
 [ 0.85128284  0.6227089  -0.80351675 -1.2711431   0.39950132 -0.69113916
   2.042885

Epoch:77/10000 Loss:0.230 Accuracy:0.913
[[-0.34179708  1.3441107   0.6126075  -0.6148716  -0.04467934 -0.9731598
  -1.0582663   2.0099487  -2.2587857  -1.5372558 ]
 [-0.21741888 -0.94169575 -1.313215    0.20118126 -2.4093804   0.38419607
   2.1324034  -1.9390726   1.3545052  -0.36936653]
 [ 0.7233039   0.00381757 -0.3476689   0.65245056 -0.8373961   0.83061844
  -0.4370282   0.00878027 -0.53273916 -1.9160799 ]
 [ 1.0440699   0.70542985 -0.9722657  -1.1027385   0.6037658  -0.869852
   1.8618559  -0.00453265 -0.4632787  -0.09381912]]
Epoch:78/10000 Loss:0.218 Accuracy:0.913
[[-0.34181947  1.3442327   0.61257416 -0.6148389  -0.044762   -0.9729643
  -1.0582348   2.0097175  -2.2586946  -1.5369507 ]
 [-0.21704766 -0.94114983 -1.3137965   0.20155539 -2.4092107   0.38443545
   2.1322286  -1.9396906   1.3542906  -0.3690217 ]
 [ 0.723705    0.00408809 -0.34817082  0.65272033 -0.83706707  0.8304736
  -0.4372183   0.00849848 -0.53298384 -1.9161894 ]
 [ 1.044966    0.7061911  -0.97345066 -1.102075

Epoch:187/10000 Loss:0.096 Accuracy:0.953
[[-0.34990013  1.3446591   0.62034065 -0.61797374 -0.05311111 -0.9635085
  -1.054428    2.0062726  -2.2536592  -1.5244489 ]
 [-0.20794049 -0.9265048  -1.3308498   0.2106701  -2.406194    0.39102656
   2.1299198  -1.9564651   1.3494257  -0.3592844 ]
 [ 0.7410387   0.00352686 -0.3653979   0.65949076 -0.81923     0.80856466
  -0.44495407  0.01391253 -0.54184973 -1.9468998 ]
 [ 1.0719465   0.71160024 -1.0026712  -1.0889995   0.6305097  -0.89708793
   1.8488672  -0.00440583 -0.48122585 -0.13382682]]
Epoch:188/10000 Loss:0.096 Accuracy:0.953
[[-0.3499418   1.3446826   0.6203693  -0.617982   -0.05315981 -0.96343917
  -1.0544075   2.0062318  -2.253644   -1.5243576 ]
 [-0.20794274 -0.9264629  -1.3308766   0.21068315 -2.4062135   0.39106706
   2.1299298  -1.9565197   1.3494271  -0.3592268 ]
 [ 0.7411697   0.00353208 -0.36554512  0.65954155 -0.8191091   0.80841357
  -0.44500092  0.01393404 -0.5418993  -1.9471147 ]
 [ 1.0720212   0.71152365 -1.0027026  -1.

Epoch:282/10000 Loss:0.077 Accuracy:0.953
[[-0.3530626   1.3459587   0.62288886 -0.61873776 -0.05650889 -0.9588392
  -1.0530292   2.003916   -2.252695   -1.5182981 ]
 [-0.20897803 -0.9244352  -1.3311956   0.21095677 -2.4079425   0.3937474
   2.1307197  -1.9592979   1.3497714  -0.3554784 ]
 [ 0.7523117   0.00598996 -0.37976828  0.66437984 -0.8099424   0.7974743
  -0.44851112  0.01261901 -0.5452178  -1.9615885 ]
 [ 1.0747828   0.7043914  -1.0007979  -1.0900896   0.6360091  -0.9081058
   1.8465669   0.00641784 -0.48253042 -0.15374956]]
Epoch:283/10000 Loss:0.077 Accuracy:0.953
[[-0.35309038  1.3459656   0.6229148  -0.61874574 -0.05653615 -0.958803
  -1.0530181   2.0039022  -2.2526882  -1.5182512 ]
 [-0.20899169 -0.9244243  -1.3311886   0.2109552  -2.4079585   0.39376837
   2.1307266  -1.959314    1.3497752  -0.35544974]
 [ 0.7524218   0.00602933 -0.3799225   0.6644314  -0.8098604   0.7973774
  -0.4485431   0.01258236 -0.5452418  -1.961705  ]
 [ 1.0747818   0.7043159  -1.0007416  -1.090112

[[-0.35558018  1.3462893   0.6254887  -0.6195459  -0.05881806 -0.9558056
  -1.0520853   2.003086   -2.252203   -1.5144631 ]
 [-0.21034418 -0.9237651  -1.3301638   0.21066935 -2.409352    0.39550564
   2.1313155  -1.9603453   1.3500843  -0.3531484 ]
 [ 0.76243794  0.01020712 -0.39464056  0.669267   -0.8028071   0.7886761
  -0.45144385  0.00824523 -0.54670393 -1.9714766 ]
 [ 1.0733181   0.6971492  -0.99363524 -1.092725    0.6376037  -0.9124845
   1.8460773   0.01642648 -0.48311725 -0.16499135]]
Epoch:380/10000 Loss:0.065 Accuracy:0.967
[[-0.35560495  1.34629     0.62551653 -0.6195546  -0.05883935 -0.95577765
  -1.0520763   2.0030818  -2.2521994  -1.5144289 ]
 [-0.21035866 -0.92376125 -1.3301502   0.2106653  -2.4093654   0.39552188
   2.1313212  -1.9603521   1.3500869  -0.3531277 ]
 [ 0.7625369   0.01025239 -0.39479136  0.6693158  -0.8027407   0.7885894
  -0.451473    0.00819514 -0.5467114  -1.9715687 ]
 [ 1.073294    0.69707686 -0.9935508  -1.0927547   0.6376119  -0.912511
   1.8460772  

...

[[-0.40696153  1.2828026   0.7235377  -0.62988394 -0.04720232 -0.90783876
  -1.0601423   1.9542737  -2.137814   -1.3201635 ]
 [-0.28438824 -1.008943   -1.1969194   0.18266127 -2.4094718   0.45857877
   2.1398     -1.9819773   1.439845   -0.15848783]
 [ 0.9078055   0.03347975 -0.5769702   0.76164323 -0.6644649   0.61625856
  -0.5573901  -0.14796609 -0.3270416  -2.005213  ]
 [ 1.1295168   0.6380452  -1.0179354  -1.0610757   0.7317497  -1.0083241
   1.785286   -0.0325855  -0.31718946 -0.16084567]]
Epoch:9404/10000 Loss:0.042 Accuracy:0.987
[[-0.4077442   1.2820685   0.72431934 -0.63049555 -0.04794928 -0.90707546
  -1.0593773   1.9550394  -2.1385295  -1.3193874 ]
 [-0.28516686 -1.0096729  -1.1961417   0.18205269 -2.410213    0.45933753
   2.140561   -1.9812163   1.4391334  -0.15771793]
 [ 0.90704167  0.03276243 -0.57620734  0.7610462  -0.6651946   0.61700374
  -0.5566437  -0.14721867 -0.3277398  -2.0044532 ]
 [ 1.1287442   0.6373197  -1.0171636  -1.0616788   0.7310125  -1.0075703
   1.7860

[[-0.40763497  1.2805109   0.7250451  -0.629681   -0.04624024 -0.9072747
  -1.0602696   1.9528236  -2.1337705  -1.3147577 ]
 [-0.28584805 -1.0119613  -1.1946298   0.18223926 -2.4092636   0.4598762
   2.140394   -1.9826401   1.4431369  -0.15235294]
 [ 0.90861624  0.03256107 -0.5769361   0.7630144  -0.6620595   0.61536574
  -0.55898285 -0.15088749 -0.32158896 -2.0012279 ]
 [ 1.1300473   0.6368653  -1.0176208  -1.0599173   0.7338859  -1.0089415
   1.783932   -0.03522365 -0.31200475 -0.15659711]]
Epoch:9535/10000 Loss:0.040 Accuracy:0.987
[[-0.40769213  1.2804507   0.72510535 -0.62972206 -0.04628894 -0.9072193
  -1.0602168   1.9528718  -2.1338053  -1.3146834 ]
 [-0.2858996  -1.0120163  -1.1945751   0.18220244 -2.4093068   0.459926
   2.140441   -1.9825976   1.4431075  -0.15228431]
 [ 0.90856904  0.03251006 -0.5768858   0.762981   -0.6620985   0.6154114
  -0.5589399  -0.1508492  -0.32161424 -2.001163  ]
 [ 1.1299832   0.6367985  -1.0175537  -1.0599637   0.73383045 -1.0088793
   1.7839913  -

Epoch:9667/10000 Loss:0.043 Accuracy:0.987
[[-0.4082432   1.278888    0.72617406 -0.6296946  -0.0458142  -0.9067347
  -1.060128    1.9521443  -2.1314545  -1.3112484 ]
 [-0.28645462 -1.0135844  -1.1934999   0.18221883 -2.4088304   0.4603938
   2.1405017  -1.9833156   1.4454482  -0.14885885]
 [ 0.90894884  0.0318066  -0.5767395   0.7637356  -0.66071725  0.6149827
  -0.5597717  -0.15249832 -0.31838217 -1.9986191 ]
 [ 1.1290934   0.6349138  -1.0161455  -1.0601856   0.733981   -1.0080646
   1.7843864  -0.03555295 -0.31001762 -0.15275787]]
Epoch:9668/10000 Loss:0.044 Accuracy:0.980
[[-0.40721405  1.2798287   0.7251578  -0.6288875  -0.04480679 -0.9077383
  -1.0611464   1.951108   -2.1304471  -1.312204  ]
 [-0.28541502 -1.0126346  -1.1945266   0.18303421 -2.407815    0.45938063
   2.139473   -1.9843615   1.4464653  -0.14982219]
 [ 0.91000384  0.03277181 -0.5777813   0.76456314 -0.65968364  0.61395353
  -0.5608155  -0.15356077 -0.31734967 -1.9996015 ]
 [ 1.1301502   0.63588065 -1.0171891  -1.05

[[-0.40795442  1.2773432   0.7267862  -0.6286584  -0.04381378 -0.907087
  -1.0611361   1.9495952  -2.1261325  -1.3063873 ]
 [-0.28712595 -1.0160143  -1.1919327   0.18249553 -2.407754    0.46093076
   2.140376   -1.9849029   1.4498489  -0.14309868]
 [ 0.91083467  0.03174265 -0.5777122   0.76601446 -0.6571607   0.6130598
  -0.5623587  -0.15663305 -0.3115432  -1.9952886 ]
 [ 1.1306598   0.63455266 -1.0167993  -1.0581348   0.737225   -1.0096601
   1.7820679  -0.0393656  -0.3034841  -0.14913015]]
Epoch:9802/10000 Loss:0.040 Accuracy:0.987
[[-0.40831497  1.2770015   0.7271469  -0.6289305  -0.04415911 -0.906736
  -1.0607804   1.9499447  -2.1264548  -1.3060235 ]
 [-0.28748545 -1.0163549  -1.191573    0.18222421 -2.4080975   0.46128038
   2.1407304  -1.9845545   1.4495275  -0.14273663]
 [ 0.9104763   0.0314028  -0.5773537   0.76574403 -0.6575042   0.6134087
  -0.5620053  -0.15628554 -0.31186363 -1.9949262 ]
 [ 1.130288    0.6342003  -1.0164275  -1.0584152   0.7368688  -1.0092982
   1.782434   -

Epoch:9911/10000 Loss:0.040 Accuracy:0.987
[[-0.40830782  1.2760159   0.72762877 -0.62847936 -0.043213   -0.9067905
  -1.0611836   1.9487404  -2.1237361  -1.3032789 ]
 [-0.28765616 -1.0175077  -1.1909128   0.18253735 -2.4073205   0.46139374
   2.140488   -1.9855783   1.4520746  -0.13983001]
 [ 0.91135776  0.03122607 -0.57773924  0.76686513 -0.65570444  0.612497
  -0.5632677  -0.15835722 -0.30831507 -1.9930182 ]
 [ 1.130451    0.63335425 -1.016099   -1.0578424   0.73797053 -1.0095077
   1.7818688  -0.04036069 -0.3009497  -0.14615898]]
Epoch:9912/10000 Loss:0.040 Accuracy:0.987
[[-0.40826395  1.2760494   0.7275888  -0.6284427  -0.0431635  -0.90683347
  -1.06123     1.9486885  -2.1236753  -1.3033016 ]
 [-0.2876155  -1.0174772  -1.1909497   0.18257155 -2.4072742   0.4613539
   2.1404448  -1.9856269   1.4521323  -0.13984953]
 [ 0.911397    0.0312553  -0.57777464  0.7668983  -0.6556594   0.6124584
  -0.56330943 -0.15840456 -0.30825865 -1.9930364 ]
 [ 1.1304882   0.6333815  -1.0161324  -1.057